In [6]:
!pip install folium
!pip install geopandas
!pip install mysql-connector-python
!pip install matplotlib

DEPRECATION: Python 2.7 will reach the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 won't be maintained after that date. A future version of pip will drop support for Python 2.7. More details about Python 2 support in pip, can be found at https://pip.pypa.io/en/latest/development/release-process/#python-2-support
You should consider upgrading via the 'pip install --upgrade pip' command.
DEPRECATION: Python 2.7 will reach the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 won't be maintained after that date. A future version of pip will drop support for Python 2.7. More details about Python 2 support in pip, can be found at https://pip.pypa.io/en/latest/development/release-process/#python-2-support
You should consider upgrading via the 'pip install --upgrade pip' command.
DEPRECATION: Python 2.7 will reach the end of its life on January 1st, 2020. Please upgrade your Python as Python 2.7 won't be maintained after that dat

In [7]:
import os
import folium
import geopandas as gpd
import numpy as np
import pandas as pd
import mysql.connector
import matplotlib.pyplot as plt
from folium import plugins

In [8]:
mydb= mysql.connector.connect(host="127.0.0.1", user="root", passwd="***", database="atlasmeasure")
measurement_loc1= pd.read_sql("SELECT * FROM measurement_loc1", con=mydb)
#Importing the table from MySQL
#Converting the datatypes to numeric for plotting
measurement_loc1.latitude=pd.to_numeric(measurement_loc1.latitude, downcast='float')
measurement_loc1.longitude=pd.to_numeric(measurement_loc1.longitude, downcast='float')
#Saving the month and year for each row
measurement_loc1['month'] = pd.DatetimeIndex(measurement_loc1['timestamp']).month
measurement_loc1['year'] = pd.DatetimeIndex(measurement_loc1['timestamp']).year
#Each unique timestamp corresponds to a particular traceroute when looking at consecutive rows
timestamps=measurement_loc1.timestamp.unique()
print(len(timestamps))
measurement_loc1.info()
print(measurement_loc1.groupby(['month']).agg(['count']))#Number of rows corresponding to each month

29580
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 606467 entries, 0 to 606466
Data columns (total 6 columns):
country      606467 non-null object
timestamp    606467 non-null datetime64[ns]
latitude     606467 non-null float32
longitude    606467 non-null float32
month        606467 non-null int64
year         606467 non-null int64
dtypes: datetime64[ns](1), float32(2), int64(2), object(1)
memory usage: 23.1+ MB
      country timestamp latitude longitude   year
        count     count    count     count  count
month                                            
1       62948     62948    62948     62948  62948
2       17122     17122    17122     17122  17122
4       60376     60376    60376     60376  60376
5       59696     59696    59696     59696  59696
6       56756     56756    56756     56756  56756
7       57418     57418    57418     57418  57418
8       60978     60978    60978     60978  60978
9       48101     48101    48101     48101  48101
10      39384     39384    3

In [9]:
coord=[] #list containing lists->corresponding to each traceroute(list of latitude and longitude)
for time in timestamps:
    df_s=measurement_loc1[measurement_loc1["timestamp"]==time]#Check for particular time
    df_sel=df_s[df_s["month"]==9]#Check for month
    trace=[]
    prev_ind=0
    for ind, row in df_sel.iterrows():
        if(ind!=prev_ind+1 and prev_ind!=0):#Check for rows being consecutive
            coord.append(trace)
            trace=[]
        trace.append([row.latitude,row.longitude])
        prev_ind=ind
    coord.append(trace)

print(len(coord))

31294


In [10]:
m = folium.Map([0, 0], zoom_start=3)

coord=[x for x in coord if x != []]#Removing empty lists from coord
print(len(coord))
for l in range(len(coord)):
    
    danger_line = folium.PolyLine(
        coord[l],
        weight=10,
        color='orange',
        opacity=0.1
    ).add_to(m)

    attr = {'fill': 'green'}

    plugins.PolyLineTextPath(
        danger_line,
        '\u25BA',
        repeat=True,
        offset=6,
        attributes=attr
    ).add_to(m)
    #print(l)

tooltip = 'Click me!'
folium.Marker([47, 8], popup='<i>emanicslab1.csg.uzh.ch</i>', tooltip=tooltip).add_to(m)
#m.save(os.path.join('results', 'PolyLineTextPath.html'))
m.save( 'september_measurement1.html')

m

4997
